In [7]:
import numpy as np
import pandas as pd
import scipy 
import matplotlib.pyplot as plt 
from scipy.stats import norm, binom, uniform
from scipy.special import logsumexp

%run tools.py

# Exercise 1 (Statistical Rethinking, McElreath et al, Chapter 5)


In [8]:
data = pd.read_csv('./milk_clean.csv',sep=',')
print(data.columns)

Index(['Unnamed: 0', 'clade', 'species', 'kcal.per.g', 'perc.fat',
       'perc.protein', 'perc.lactose', 'mass', 'neocortex.perc'],
      dtype='object')


In [9]:
!cat tools.py

import numpy as np 
import matplotlib.pyplot as plt
import pandas as pd

from scipy.optimize import minimize
from scipy.stats import norm, uniform, binom
from scipy.stats import gaussian_kde
from scipy.stats import multivariate_normal

def laplace_solution(params, other_params, data, lik, priors):
  
    def evaluate_log_post(params, other_params, data, lik, priors):
        model_list = { 'gaussian' : norm, 'uniform': uniform, 'binomial' : binom}
    
        model_lik = model_list[lik]
    
        #Computing log-priors
        log_prior = 0
        for i,mod in enumerate(priors):
            log_prior += model_list[mod[0]].logpdf(params[i], *mod[1])

            
        #Computing log-likelihood
        if lik == 'gaussian':
            # Dirty trick for guaranteeing positive variance
            params[-1] = np.abs(params[-1])
                
        if len(other_params)>0:
            log_lik = np.sum([model_list[lik].logpdf(point, *(params,other_params)) for point in data])
   


**1) Analyze the relationship of milk energy with respect to percentage fat and percentage lactose through two independent linear regressions. Comment.**


\begin{align}
Kcd &= a + b * \text{perc.fat}\\
Kcd &\approx N(a+b*\text{perc.fat}, \sigma)
\end{align}

**2) What happens if we regress kcal.per.g with respect to both perc.fat and perc.lactose ?**

In [ ]:
expr = 'kcal.per.g ~ perc.fat + perc.lactose'

**3) Can you explain the differences observed between the results of questions 1 and 2 ?**

In [ ]:
fields = ['kcal.per.g', 'perc.fat', 'perc.lactose']

plt.figure(figsize=(8,8))

for i, field in enumerate(fields):
    
    for j in range(len(fields)):
    
        plt.subplot(len(fields), len(fields), len(fields)*i + j + 1)
        
        if i==j:
            plt.text(0.25,0.5, field, fontsize=15)
            plt.xticks([])
            plt.yticks([])
        else:
            plt.scatter(data[fields[j]],data[field])

In [ ]:
from scipy.stats import pearsonr


**4) Study the effect of correlation between predictors**

To answer this question you will create a dummy variable whose correlation with perc.fat varies. Then you will fit many linear regressions (let's say 10) using these two variables and observe the effect on the mean standard deviation of b_fat.

In [ ]:
corr = np.linspace(0., 0.99, 10)
print(corr)
std_err_list = []

for coeff in corr:
    data['x'] = np.random.normal(
        loc=coeff*np.mean(data['perc.fat']), 
        scale=np.sqrt((1-coeff**2))*np.std(data['perc.fat']), 
        size=data['perc.fat'].shape
    )
    
    temp_list = []
    
    for _ in range(500):
    
        expr = 'kcal.per.g ~ perc.fat + x'

        # Initializing the likelihood
        likelihood = 'gaussian'

        # Defining the prior with hyperparameters 
        prior_a_mean = 0.5
        prior_a_sigma = 10
        prior_a = ['gaussian', [prior_a_mean, prior_a_sigma]]

        prior_b_fat_mean = 0
        prior_b_fat_sigma = 1
        prior_b_fat = ['gaussian', [prior_b_fat_mean, prior_b_fat_sigma]]

        prior_c_mean = 0
        prior_c_sigma = 1
        prior_c = ['gaussian', [prior_c_mean, prior_c_sigma]]

        sigma_inf = 0
        sigma_sup = 10
        prior_sigma_unif = [sigma_inf, sigma_sup]
        prior_sigma = ['uniform', prior_sigma_unif]

        priors = [prior_a, prior_b_fat, prior_c, prior_sigma]

        solution_regression = laplace_solution_regression(expr, data, likelihood, priors)

        posterior_samples = post_sample_Laplace(solution_regression, 1000)
        temp_list.append(np.std(posterior_samples[:,1]))
        
    std_err_list.append(np.mean(temp_list))

[0.   0.11 0.22 0.33 0.44 0.55 0.66 0.77 0.88 0.99]
      fun: -12.244019682092308
 hess_inv: array([[ 2.42609489e-03, -5.80285349e-05,  3.48422784e-06,
         8.93124428e-06],
       [-5.80285349e-05,  1.60398804e-06,  2.54395715e-08,
        -3.41462244e-07],
       [ 3.48422784e-06,  2.54395715e-08,  1.77587516e-06,
        -6.05969853e-07],
       [ 8.93124428e-06, -3.41462244e-07, -6.05969853e-07,
         1.63955675e-04]])
      jac: array([2.38418579e-07, 8.22544098e-06, 2.38418579e-06, 9.53674316e-07])
  message: 'Optimization terminated successfully.'
     nfev: 245
      nit: 41
     njev: 49
   status: 0
  success: True
        x: array([0.28674174, 0.0103976 , 0.00147068, 0.07636356])


/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0


      fun: -12.244019682127863
 hess_inv: array([[ 2.10155960e-03, -4.71911200e-05, -5.85119318e-06,
         2.85531665e-05],
       [-4.71911200e-05,  1.25028780e-06,  3.58208103e-07,
        -1.08970848e-06],
       [-5.85119318e-06,  3.58208103e-07,  1.49635768e-06,
         2.18114860e-06],
       [ 2.85531665e-05, -1.08970848e-06,  2.18114860e-06,
         1.49923837e-04]])
      jac: array([ 3.50475311e-05,  2.16758251e-03, -1.20186806e-03, -1.08480453e-04])
  message: 'Desired error not necessarily achieved due to precision loss.'
     nfev: 407
      nit: 37
     njev: 79
   status: 2
  success: False
        x: array([0.28674169, 0.01039761, 0.00147068, 0.07636354])


/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0


      fun: -12.244019682625236
 hess_inv: array([[ 2.33495524e-03, -5.28732791e-05,  1.15471432e-05,
        -4.44462310e-05],
       [-5.28732791e-05,  1.42455314e-06, -1.62966449e-07,
         1.39519755e-06],
       [ 1.15471432e-05, -1.62966449e-07,  1.69273771e-06,
         1.34592711e-06],
       [-4.44462310e-05,  1.39519755e-06,  1.34592711e-06,
         1.62391440e-04]])
      jac: array([2.93254852e-05, 1.27784014e-02, 4.66442108e-03, 2.21967697e-04])
  message: 'Desired error not necessarily achieved due to precision loss.'
     nfev: 467
      nit: 42
     njev: 90
   status: 2
  success: False
        x: array([0.28674106, 0.01039762, 0.00147069, 0.0763636 ])


...

/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0


      fun: -11.768245454770966
 hess_inv: array([[ 1.20285599e-01, -1.26260343e-05, -3.31695945e-03,
        -5.17556050e-04],
       [-1.26260343e-05,  1.68540999e-06, -1.33251307e-06,
         1.25918688e-07],
       [-3.31695945e-03, -1.33251307e-06,  9.34061138e-05,
         1.42190239e-05],
       [-5.17556050e-04,  1.25918688e-07,  1.42190239e-05,
         1.64492796e-04]])
      jac: array([0.00040483, 0.02955711, 0.01986134, 0.00012589])
  message: 'Desired error not necessarily achieved due to precision loss.'
     nfev: 484
      nit: 36
     njev: 93
   status: 2
  success: False
        x: array([0.12556465, 0.01031269, 0.00445066, 0.07852871])


/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0


      fun: -11.768245441789736
 hess_inv: array([[ 1.52409646e-03, -2.38565133e-06, -3.95100070e-05,
        -5.08026582e-04],
       [-2.38565133e-06,  1.71122673e-06, -1.61491614e-06,
         7.95239035e-07],
       [-3.95100070e-05, -1.61491614e-06,  2.91720570e-06,
         1.31698269e-05],
       [-5.08026582e-04,  7.95239035e-07,  1.31698269e-05,
         1.69342426e-04]])
      jac: array([-7.15255737e-07,  1.54972076e-06,  1.54972076e-06, -2.14576721e-06])
  message: 'Optimization terminated successfully.'
     nfev: 394
      nit: 38
     njev: 76
   status: 0
  success: True
        x: array([0.12558464, 0.01031267, 0.00445012, 0.07852869])


/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0
/home/quentin/anaconda3/lib/python3.8/site-packages/scipy/optimize/_numdiff.py:557: RuntimeWarning: invalid value encountered in subtract
  df = fun(x) - f0


In [ ]:
plt.figure()
plt.plot(corr, std_err_list)
plt.xlabel('correlation')
plt.ylabel('std dev b_fat')
plt.show()

# Exercise 2  (Statistical Rethinking, McElreath et al, Chapter 6)

**1) Using the *Milk* dataset  of the previous exercise, fit four different models for describing the kcal.per.g data :**

- One with both neocortex and log_mass
- One with neocortex
- One with log_mass
- One with no predictor (an intercept only)

**For each of this model, you will compute their WAIC with standard error (SE), dWAIC with standard error (dSE), pWAIC, and the weight criteria. What can you conclude by analyzing these numbers ? You will present the results in a table.**

We denote by neocortex the variable necortex.perc / 100.

dWAIC is the difference between each WAIC and the lowest WAIC among the models.
 
The standard error (SE) of a score S is given by:

$$
SE = \sqrt{Npoints * var(S)}
$$

The weight criteria is the *Akaike weight* which is given for model i by the formula:

$$w_i = \frac{\exp(-0.5dWAIC_i)}{\sum_j \exp(-0.5dWAIC_j)}$$

In [ ]:
data['log_mass'] = np.log(data['mass'])
data['neocortex'] = data['neocortex.perc'] / 100

In [ ]:
expr = 'kcal.per.g ~ neocortex + log_mass'

N = 5000





waic_vect_model1 = 
waic_model1 = 
p_waic_model1 = 
se_model1 = 

print(waic_model1)
print(p_waic_model1)
print(se_model1)

In [ ]:
waic = np.array([waic_model1, waic_model2, waic_model3, waic_model4])
waic_vect = np.array([waic_vect_model1, waic_vect_model2, waic_vect_model3, waic_vect_model4])
p_waic = np.array([p_waic_model1, p_waic_model2, p_waic_model3, p_waic_model4])
se = np.array([se_model1, se_model2, se_model3, se_model4])

d_waic = np.zeros(waic.shape)
weights = np.zeros(waic.shape)
d_se = np.zeros(waic.shape)


summary_stats = [waic, p_waic, d_waic, weights, se, d_se]
summary_stats = pd.DataFrame(summary_stats).transpose()
summary_stats.columns = ['WAIC', 'pWAIC', 'dWAIC', 'weight', 'SE', 'd_SE']
summary_stats.index = ['model1', 'model2', 'model3', 'model4']
#summary_stats.rename(index=list(names), inplace=True)
print(summary_stats)

In [ ]:
samples = np.random.normal(loc=5.17, scale=7.46, size=100000)
print(np.sum(samples<0.)/len(samples))

**2) In order to better intepret the results of question 2, analyze the posterior estimates of the slope parameters for the different models. Present the results using box plots.**

# Exercise 3

In this exercise we will show how to use the Laplace approximation by deriving the equations on an example.

Consider a random variable $\theta$ following a uniform distribution on [0, 1]. Let's consider a dummy experiment in which two outcomes are possible (success and failure). The experiment is made n times with k successes. The experiments are independent from each other. The probability of success is given by $\theta$. We will denote by y the random variable describing the number of successes. 

**1) Write the data likelihood and the posterior distribution $p(\theta|y)$ (up to constant).**

**2) Estimate the posterior distribution $p(\theta|y)$ using the Laplace approximation. You will derive the computations yourself.**

**3) Plot the posterior pdf of $\theta$ obtained with the Laplace approximation and the true posterior.**
